In [0]:
%%capture
!pip install unsloth
# Also get the latest nightly Unsloth!
!pip uninstall unsloth -y && pip install --upgrade --no-cache-dir --no-deps git+https://github.com/unslothai/unsloth.git
!pip install openai
# !pip install vllm
!pip install mlflow

dbutils.library.restartPython()

In [0]:
from unsloth import FastLanguageModel
from unsloth.chat_templates import get_chat_template
import torch
max_seq_length = 2048 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


2025-03-04 02:02:47.403826: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1741053767.419573  147885 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1741053767.424323  147885 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-03-04 02:02:47.441627: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


🦥 Unsloth Zoo will now patch everything to make training faster!
[2025-03-04 02:02:53,608] [INFO] [real_accelerator.py:222:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/usr/bin/ld: cannot find -lcufile: No such file or directory
collect2: error: ld returned 1 exit status


In [0]:
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/Llama-3.3-70B-Instruct",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
)



==((====))==  Unsloth 2025.3.1: Fast Llama patching. Transformers: 4.48.0.
   \\   /|    GPU: NVIDIA A100 80GB PCIe. Max memory: 79.151 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.0. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post3. FA2 = True]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

In [0]:
model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = True,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth 2025.3.1 patched 80 layers with 80 QKV layers, 80 O layers and 80 MLP layers.


In [0]:
from datasets import Dataset
spdf = spark.sql("select instruction, input, answer from main.sgfs.reasoning_traces_quant_distill_r1_llama70b where answer is not null")
dataset = Dataset.from_spark(spdf)
spdf.display()

instruction input answer Answer the following question after understanding the specifics of the vehicle in question.

It is a 2000 Toyota Sienna CE 3.0L Dash lights. with the VIN 4T3GF19C2YU310996 and a mileage of 65,500 mi. This 2000 Toyota Sienna CE is a 3.0L / 6 cyl / Gas engine with 4-speed Automatic Transaxle (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Dash Lights Conditions: Shorted This vehicle has 2 separate fuses for the lights. The one that is blowing is for the dash lights. The parking light fuse is O.K. As soon as you turn on the parking light switch, it has a dead short to to the dash light fuse. I checked the switch and can't find anything wrong with it. My short finder won't stay on long enough to find the affected area. I went ahead and connected a wire across the fuse real quick to find the problem. It had some smoke come out of the harness under the dash, but couldn't tell because it was in the middle of a harness full of about 50 wires. At this point it could still be something behind the instrument panel, a component, etc. Has anyone seen this on this vehicle before? I need some info before I go any further. Alright, let's tackle this dash light issue on your 2000 Toyota Sienna step by step.

1. **Check for Aftermarket Installations**: Start by inspecting any aftermarket components like stereos or accessories near the dash. Improper wiring, especially grounding issues, can cause shorts when switches are activated.

2. **Inspect Visor Wires**: Remove the visors and check for pinched wires in the headliner, a common issue that can lead to shorts.

3. **Verify Bulbs**: Ensure all bulbs are correctly installed as incorrect types might cause unexpected electrical behavior.

4. **Review Accident History**: Consider if past accidents or repairs could have affected wiring integrity, even if unrelated at first glance.

5. **Disconnect Accessories**: If equipped with a trailer harness or similar, temporarily disconnect it to rule out external issues.

6. **Use Proper Diagnostic Tools**: Invest in a good multimeter with an amp clamp to safely and accurately trace the short without causing further damage.

By systematically checking these areas, you should be able to identify and resolve the cause of your dash light fuse blowing. Answer the following question after understanding the specifics of the vehicle in question.

It is a 1998 Isuzu Trooper S 3.5L Timing Belt. with the VIN JACDJ58X1W7905214 and a mileage of 81,000 mi. This 1998 Isuzu Trooper S is a 3.5L / 6 cyl / Gas engine with 4-speed Automatic Transmission transmission.
Delivery system: Fuel Injection Affected component: Timing Belt I am trying to set up the timing belt on this 3.5 trooper, the camshafts were turned while the timing belt was removed. I read the tsb (IB00-S005) and set the cams back the way it describes. I line up all of the lines on the timing belt and I have to turn the crankshaft 3 turns to get the timing marks to line back up on the engine. Am I doing something wrong or is this normal? Step29 of the tsb says to turn the crank a "minimum of 2 complete turns" is this saying what I think it does and I may have to turn the crank 3 times? Please help. thank you. The situation you're encountering with your 1998 Isuzu Trooper S 3.5L engine is quite normal, especially given the engine's unique timing setup. Here's a concise summary of what you need to know and do:

1. **Normal Multiple Turns**: It's normal for the timing marks to align only after more than two crankshaft rotations because each cam sprocket drives two gears, requiring additional turns to sync everything.

2. **Focus on Engine Marks**: Rely on the engine's own timing marks on the crank and cam sprockets rather than the belt's marks, as these are more critical for accurate alignment.

3. **TSB Guidance**: The TSB mentions a minimum of two turns, but it may require three or more rotations to achieve proper alignment due to the engine's design quirks.

In [0]:
system_message = """You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response"""

def create_conversation(sample):
  return {
    "messages": [
      {"role": "system", "content": system_message},
      {"role": "user", "content": f'{sample["instruction"]} \n {sample["input"]}'},
      {"role": "assistant", "content": sample["answer"]}
    ]
  }
dataset = dataset.map(create_conversation,remove_columns=dataset.features,  batched=False)

In [0]:
dataset.column_names

['messages']

In [0]:
# from unsloth import standardize_sharegpt
# dataset = standardize_sharegpt(dataset)
# from unsloth.chat_templates import get_chat_template

# tokenizer = get_chat_template(
#     tokenizer,
#     chat_template = "llama-3", # Supports zephyr, chatml, mistral, llama, alpaca, vicuna, vicuna_old, unsloth
#     mapping = {"role" : "role", "content" : "content", "user" : "user", "assistant" : "assistant"}, # openai style
# )

# def formatting_prompts_func(examples):
#     convos = examples["conversations"]
#     texts = [tokenizer.apply_chat_template(convo, tokenize = False, add_generation_prompt = False) for convo in convos]
#     return { "text" : texts, }
# pass
# formatted_dataset = dataset.map(formatting_prompts_func, remove_columns=dataset.features, batched=False)
# from unsloth.chat_templates import get_chat_template

# tokenizer = get_chat_template(
#     tokenizer,
#     chat_template="llama-3",  # Choose based on your base model
#     # No mapping needed as our data will be in the correct format
#     map_eos_token=True
# )

# def formatting_prompts_func(examples):
#     texts = []
#     for convo in examples["messages"]:
#         try:
#             if isinstance(convo, dict):
#                 # Get the formatted text as a string
#                 formatted_text = tokenizer.apply_chat_template(
#                     [convo], 
#                     tokenize=False,
#                     add_generation_prompt=False
#                 )
#                 # If formatted_text is a list, get the first item
#                 # print(type(formatted_text))
#                 if isinstance(formatted_text, list):
#                     formatted_text = formatted_text[0] if formatted_text else ""
#                 texts.append(formatted_text)
#             else:
#                 print(f"Unexpected format: {type(convo)}")
#         except Exception as e:
#             print(f"Error processing conversation: {e}")
#             # Add an empty string as fallback
#             texts.append("")
    
#     return {"text": texts}

# # Apply the transformation
# formatted_dataset = dataset.map(formatting_prompts_func, remove_columns=dataset.features, batched=False)


# formatted_df = formatted_dataset.to_pandas()
# alpaca_prompt = """Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

# ### Instruction:
# {}

# ### Input:
# {}

# ### Response:
# {}"""

# EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
# def formatting_prompts_func(examples):
#     instructions = examples["instruction"]
#     inputs       = examples["input"]
#     outputs      = examples["output"]
#     texts = []
#     for instruction, input, output in zip(instructions, inputs, outputs):
#         # Must add EOS_TOKEN, otherwise your generation will go on forever!
#         text = alpaca_prompt.format(instruction, input, output) + EOS_TOKEN
#         texts.append(text)
#     return { "text" : texts, }
# pass

# from datasets import load_dataset
# dataset = load_dataset("yahma/alpaca-cleaned", split = "train")
# dataset = dataset.map(formatting_prompts_func, batched = True,)

In [0]:
def format_chat(example):
    conversation = ""
    for message in example["messages"]:
        role = message["role"]
        content = message["content"]
        conversation += f"{role}: {content}\n\n"
    return {"text": conversation}

# Apply the formatting
formatted_dataset = dataset.map(format_chat)

In [0]:
chatml_template = """{% for message in messages %}
{% if message['role'] == 'system' %}<|system|>
{{ message['content'] }}</s>
{% elif message['role'] == 'user' %}<|user|>
{{ message['content'] }}</s>
{% elif message['role'] == 'assistant' %}<|assistant|>
{{ message['content'] }}</s>
{% endif %}
{% endfor %}
{% if add_generation_prompt %}
<|assistant|>
{% endif %}"""

# Set the chat template for the tokenizer
tokenizer.chat_template = chatml_template

In [0]:
from trl import SFTTrainer
from transformers import TrainingArguments
from unsloth import is_bfloat16_supported

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = formatted_dataset,
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    dataset_num_proc = 2,
    packing = False, # Can make training 5x faster for short sequences.
    args = TrainingArguments(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        # num_train_epochs = 1, # Set this for 1 full training run.
        max_steps = 100,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "/Volumes/main/sgfs/sg-vol/llama-33-70b/outputs",
        report_to = "none", # Use this for WandB etc
    ),
)

In [0]:
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = NVIDIA A100 80GB PCIe. Max memory = 79.151 GB.
37.629 GB of memory reserved.


In [0]:
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 1,625 | Num Epochs = 1
O^O/ \_/ \    Batch size per device = 2 | Gradient Accumulation steps = 4
\        /    Total batch size = 8 | Total steps = 100
 "-____-"     Number of trainable parameters = 207,093,760


In [0]:
#@title Show final memory and time stats
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory         /max_memory*100, 3)
lora_percentage = round(used_memory_for_lora/max_memory*100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training.")
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

1759.2199 seconds used for training.
29.32 minutes used for training.
Peak reserved memory = 40.947 GB.
Peak reserved memory for training = 3.318 GB.
Peak reserved memory % of max memory = 51.733 %.
Peak reserved memory for training % of max memory = 4.192 %.


In [0]:
messages = [
    {"role": "system", "content": "You are an agent that helps with resolving user issues with their car. Your job is to post a response in a forum, and you deeply care about ensuring that you solve the problem to the best of your ability."},
    {"role": "user", "content": "I have a 2018 Honda Civic and the check engine light just came on. The car seems to be running fine, but I'm worried. What should I do?"}
]


prompt = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)

print(prompt)
inputs = tokenizer(prompt, return_tensors = "pt").to("cuda")
FastLanguageModel.for_inference(model)
outputs = model.generate(**inputs, max_new_tokens=500)
generations = tokenizer.batch_decode(outputs)

In [0]:
def extract_assistant_response(text):
    """
    Extracts the text between the first <|assistant|> token and the first </s> or <|eot_id|> token that follows it.
    
    Args:
        text (str): The input string containing the tokens.
        
    Returns:
        str: The extracted text between <|assistant|> and the first </s> or <|eot_id|>, or None if not found.
    """
    # Find the position of the first <|assistant|> token
    assistant_start = text.find("<|assistant|>")
    
    if assistant_start == -1:
        return None  # No <|assistant|> token found
    
    # Move past the <|assistant|> token
    content_start = assistant_start + len("<|assistant|>")
    
    # Find the position of the </s> token after <|assistant|>
    end_s_token = text.find("</s>", content_start)
    
    # Find the position of the <|eot_id|> token after <|assistant|>
    end_eot_token = text.find("<|eot_id|>", content_start)
    
    # Determine which end token appears first (if any)
    if end_s_token == -1 and end_eot_token == -1:
        return None  # Neither </s> nor <|eot_id|> found
    
    if end_s_token == -1:  # Only <|eot_id|> exists
        end_token = end_eot_token
    elif end_eot_token == -1:  # Only </s> exists
        end_token = end_s_token
    else:  # Both exist, choose the earliest one
        end_token = min(end_s_token, end_eot_token)
    
    # Extract the text between <|assistant|> and the determined end token
    assistant_response = text[content_start:end_token].strip()
    
    return assistant_response

In [0]:
extract_assistant_response(generations[0])

In [0]:
# alpaca_prompt = Copied from above
# FastLanguageModel.for_inference(model) # Enable native 2x faster inference

from transformers import TextStreamer
text_streamer = TextStreamer(tokenizer)
_ = model.generate(**inputs, streamer = text_streamer, max_new_tokens = 500)

<|begin_of_text|><|system|>
You are an agent that helps with resolving user issues with their car. Your job is to post a response in a forum, and you deeply care about ensuring that you solve the problem to the best of your ability.</s>
<|user|>
I have a 2018 Honda Civic and the check engine light just came on. The car seems to be running fine, but I'm worried. What should I do?</s>
<|assistant|>
If your 2018 Honda Civic's check engine light has come on, here are some steps you can take:

1. **Use an OBD-II Scanner**: Start by using an OBD-II scanner to retrieve the trouble codes from your car's onboard computer. This will give you specific information about what's causing the issue.

2. **Check the Basics**: Before taking it to a mechanic, check simple things like your gas cap. A loose or damaged cap can trigger the check engine light.

3. **Consider Common Issues**: For your model year, common issues include problems with the VSA system, fuel injectors, or the catalytic converter. If

In [0]:
save_loc = '/Volumes/main/sgfs/sg-vol/llama-33-70b/llama33-70b-automotive-agent-final'
trainer.model.save_pretrained(save_loc)
tokenizer.save_pretrained(save_loc)

('/Volumes/main/sgfs/sg-vol/llama-33-70b/llama33-70b-automotive-agent-final/tokenizer_config.json',
 '/Volumes/main/sgfs/sg-vol/llama-33-70b/llama33-70b-automotive-agent-final/special_tokens_map.json',
 '/Volumes/main/sgfs/sg-vol/llama-33-70b/llama33-70b-automotive-agent-final/tokenizer.json')

In [0]:
%sql
CREATE VOLUME IF NOT EXISTS main.sgfs.finetunes;

In [0]:
import mlflow
import numpy as np
import os

CATALOG = "main"
SCHEMA = "sgfs"
MODEL_NAME = "llama_3_3_70B_unsloth"
VOLUME = "finetunes"
ENDPOINT_NAME = MODEL_NAME

MODEL_PATH = f"{CATALOG}.{SCHEMA}.{MODEL_NAME}"
VOLUME_PATH = f"/Volumes/{CATALOG}/{SCHEMA}/{VOLUME}"

CHECKPOINT_PATH = os.path.join(VOLUME_PATH, "llama33-70b-chatauto-merged")

mlflow.set_registry_uri('databricks-uc')

In [0]:
model.save_pretrained_merged(CHECKPOINT_PATH, tokenizer, save_method="merged_16bit")

Unsloth: Merging 4bit and LoRA weights to 16bit...
Unsloth: Will use up to 125.79 out of 208.71 RAM for saving.
Unsloth: Saving model... This might take 5 minutes ...


 12%|█▎        | 10/80 [00:00<00:03, 19.58it/s]
We will save to Disk and not RAM now.
100%|██████████| 80/80 [1:05:29<00:00, 49.12s/it]


Unsloth: Saving tokenizer... Done.
Done.


In [0]:
eval_df = spark.sql("select * from main.sgfs.forum_eval_canonical_data_generated").toPandas()

In [0]:
messages = [
    {"role": "system", "content": "You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response"},
    {"role": "user", "content": "I have a 2018 Honda Civic and the check engine light just came on. The car seems to be running fine, but I'm worried. What should I do?"}
]


with mlflow.start_run():  
    mlflow.transformers.log_model(
        # transformers_model=components,
        transformers_model = CHECKPOINT_PATH,
        artifact_path="model",
        task="llm/v1/completions",
        input_example=messages,
        registered_model_name=MODEL_PATH,
    )

In [0]:
print(eval_df.instruction.iloc[0])
print(eval_df.input.iloc[0])


Answer the following question after understanding the specifics of the vehicle in question.

It is a 1997 BMW 740iL 4.4L Rear Door Locks, Gas Door. with the VIN WBAGJ8325VDL40880 and a mileage of 165,555 mi. This 1997 BMW 740iL is a 4.4L / 8 cyl / Gas engine with 5-speed Automatic Transmission (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Rear Door Locks, Gas Door
Customer has no operating rear door locks or gas door. The central locking system will not comm. with the assenmacher retriever. All fuses are good. I need a strategy for pin testing the central locking module in dash.


You can do this later when you need to score the model

In [0]:
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = CHECKPOINT_PATH,
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
)


==((====))==  Unsloth 2025.3.1: Fast Llama patching. Transformers: 4.48.0.
   \\   /|    GPU: NVIDIA A100 80GB PCIe. Max memory: 79.151 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.0. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post3. FA2 = True]
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Loading checkpoint shards:   0%|          | 0/30 [00:00<?, ?it/s]

In [0]:
def generate_response(user_content, system_prompt="You are an agent that helps with resolving user issues with their car. Your job is to post a response in a forum, and you deeply care about ensuring that you solve the problem to the best of your ability."):
    """Generate a response for a given user content"""
    messages = [
        {"role": "system", "content": system_prompt},
        {"role": "user", "content": user_content}
    ]
    
    prompt = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    inputs = tokenizer(prompt, return_tensors="pt").to("cuda")
    
    FastLanguageModel.for_inference(model)
    outputs = model.generate(**inputs, max_new_tokens=1500)
    generation = tokenizer.batch_decode(outputs)[0]
    # print(generation)
    # Extract just the assistant's response (assuming the format includes the prompt)
    # This may need adjustment based on your specific tokenizer's output format
    response = extract_assistant_response(generation)
    return response


In [0]:
print(generate_response(user_content="""Answer the following question after understanding the specifics of the vehicle in question.

It is a 1997 BMW 740iL 4.4L Rear Door Locks, Gas Door. with the VIN WBAGJ8325VDL40880 and a mileage of 165,555 mi. This 1997 BMW 740iL is a 4.4L / 8 cyl / Gas engine with 5-speed Automatic Transmission (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Rear Door Locks, Gas Door
Customer has no operating rear door locks or gas door. The central locking system will not comm. with the assenmacher retriever. All fuses are good. I need a strategy for pin testing the central locking module in dash."""))

<|begin_of_text|><|system|>
You are an agent that helps with resolving user issues with their car. Your job is to post a response in a forum, and you deeply care about ensuring that you solve the problem to the best of your ability.</s>
<|user|>
Answer the following question after understanding the specifics of the vehicle in question.

It is a 1997 BMW 740iL 4.4L Rear Door Locks, Gas Door. with the VIN WBAGJ8325VDL40880 and a mileage of 165,555 mi. This 1997 BMW 740iL is a 4.4L / 8 cyl / Gas engine with 5-speed Automatic Transmission (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Rear Door Locks, Gas Door
Customer has no operating rear door locks or gas door. The central locking system will not comm. with the assenmacher retriever. All fuses are good. I need a strategy for pin testing the central locking module in dash.</s>
<|assistant|>
To address the issue with the rear door locks and gas door on your 1997 BMW 740iL, I'll provide a step-by-step strate

In [0]:
def generate_prompt(task, query):
    """
    Generate a forum response prompt based on the provided task and query.

    Parameters:
    - task (str): The specific task to be performed.
    - query (str): The user's query from the automotive forum.

    Returns:
    - str: The formatted prompt string.
    """
    prompt_template = (
        "Using the <TASK>, <QUERY> posted by a user in an automotive forum, "
        "provide the best possible response for the <QUERY>. "
        "Structure it in a way that's most useful to the person posting the <QUERY> just like how someone will post a response in an online forum. "
        "Don't include finishing signatures or human names.\n\n"
        "<TASK>\n"
        "{task}\n"
        "</TASK>\n\n"
        "<QUERY>\n"
        "{query}\n"
        "</QUERY>"
    )
    
    return prompt_template.format(task=task, query=query)

In [0]:
eval_df['prompt']=eval_df.apply(lambda x: generate_prompt(x['instruction'], x['input']), axis=1)

In [0]:
eval_df['response']=eval_df.prompt.apply(generate_response)

In [0]:
spark.createDataFrame(eval_df).write.mode("overwrite").saveAsTable("main.sgfs.eval_response_peft_model")

In [0]:
%sql
select response as peft_response, a.answer as canon_answer, b.answer AS ft_answer from main.sgfs.eval_response_peft_model a
inner join main.sgfs.forum_eval_canonical_data_llama_ft b on a.row_id = b.row_id

peft_response canon_answer ft_answer To tackle the issue with the rear door locks and gas door not operating, and the central locking system not communicating with the Assenmacher retriever, we'll need to dive into the electrical system of your 1997 BMW 740iL. Given that all fuses are good, our focus will shift towards the central locking module, which is likely the brain behind the locking system's operation.

First, it's essential to consult the wiring diagram specific to your vehicle's make, model, and year. This will provide a clear map of how the central locking module communicates with other components, including the rear door locks and the gas door. The VIN you provided, WBAGJ8325VDL40880, can help ensure you're looking at the correct diagram, as wiring can vary slightly even within the same model year based on production date and optional equipment.

The central locking module, often located in the dashboard or under the steering column, is usually connected to the car's computer system and receives input from various sensors and switches (like the door switches and the central locking button). It then sends output signals to actuators (like the door lock motors and the gas door release).

For pin testing the central locking module, you'll need a multimeter and possibly a wiring diagram that highlights the module's connector pins. Here's a general strategy:

1. **Identify the Module and Its Connector**: Locate the central locking module and its electrical connector. This might require removing trim pieces or the glove box to access.

2. **Consult the Wiring Diagram**: Use the wiring diagram to identify which pins on the connector are associated with the rear door locks and the gas door. Typically, these diagrams are color-coded and can tell you which wire (and thus which pin) is responsible for which function.

3. **Power On and Testing**:
 - With the ignition in the "on" position (but the car not started), use your multimeter to check for voltage at the appropriate pins for the rear door locks and gas door. If you're testing for a signal from the module to the actuators, you might be looking for a pulse or a specific voltage level when the central locking button is pressed.
 - If you find voltage where it should be, the issue might be with the actuators themselves or the wiring between the module and the actuators.
 - If there's no voltage, the problem could be within the central locking module, the wiring, or the control circuit (including switches and sensors).

4. **Ground Testing**: Ensure that the ground circuit for the central locking module and its associated components is good. A faulty ground can prevent the system from working properly.

5. **Signal Testing**: If possible, use an oscilloscope to look at the signal quality coming from the central locking module to the actuators. This can help identify if there's noise on the line or if the signal is not reaching its destination.

6. **Consult a Professional**: If you're not comfortable with this level of electrical diagnosis, or if after testing you're still unsure of the cause, it may be best to consult a professional mechanic or an auto electrician who specializes in BMWs. They will have the necessary experience and possibly specific tools to diagnose and repair the issue efficiently.

Remember, safety first: Ensure you're working in a well-ventilated area, away from any flammable materials, and consider having a fire extinguisher nearby. Also, be cautious not to short circuit any components, as this can cause damage to the vehicle's electrical system. Based on your symptoms with the rear door locks and gas door not operating, here are some troubleshooting steps to follow:

1. First, check the fuses in the trunk near the battery. The fuel door actuator often blows a fuse when it fails, which can disable multiple central locking functions. When checking fuses, be careful as these blade-type fuses can sometimes crack rather than completely blow, giving false 

In [0]:
%sql
CREATE OR REPLACE TABLE main.sgfs.auto_judgements_peft AS
with comparison_data as 
(
select response as peft_response, a.answer as canon_answer, b.answer AS ft_answer from main.sgfs.eval_response_peft_model a
inner join main.sgfs.forum_eval_canonical_data_llama_ft b on a.row_id = b.row_id)
SELECT 
  *,
  ai_query(
    'sg-external', -- this time around we use the latest gpt-4o model70000
    CONCAT(
      'The following is a comparison of the generated responses from the peft model and the fine-tuned model.',
      'peft model answer:', peft_response, -- peft model
      'fine-tuned answer:', ft_answer, -- fine tuning
      'canonical answer:', canon_answer, -- know it all
      'Your job is to compare the peft model answer with the canonical answer first and produce a score called ''peft_score'' based on how similar they are. Then compare the fine-tuned model answer with the canonical answer and produce a score called ''ft_score''. ',
      'The score should be a number between 0 and 100. The higher the score, the more similar they are. Similarity is based on the coverage of facts in the canonical answer. Similar facts produces a higher score.'
      'Finally produce the following JSON output: {"peft_score": <peft_score> , "ft_score": <ft_score>, "peft_score_reasoning": <peft_score_reasoning>, "ft_score_reasoning": <ft_score_reasoning>}. These are the only keys you need to produce in the JSON. Do not pack the JSON response inside a ```json``` tag. Only produce the JSON and nothing else.'
    )
  ) AS ai_result
FROM comparison_data;

num_affected_rows num_inserted_rows

In [0]:
%sql
create or replace view main.sgfs.auto_judgements_peft_vw as
select 
get_json_object(ai_result,'$.peft_score') as peft_score,
get_json_object(ai_result,'$.ft_score') as ft_score,
get_json_object(ai_result,'$.peft_score_reasoning') as peft_score_reasoning,
get_json_object(ai_result,'$.ft_score_reasoning') as ft_score_reasoning
from main.sgfs.auto_judgements_peft;

In [0]:
%sql
select 
avg(peft_score) as avg_peft_score,
avg(ft_score) as avg_ft_score,
median(peft_score) as median_peft_score,
median(ft_score) as median_ft_score,
round((avg(ft_score) - avg(peft_score))/avg(peft_score) * 100) as avg_improvement_percent,
round((median(ft_score) - median(peft_score))/median(peft_score) * 100) as median_improvement_percent
from main.sgfs.auto_judgements_peft_vw;

avg_peft_score avg_ft_score median_peft_score median_ft_score avg_improvement_percent median_improvement_percent 66.8 55.0 70.0 60.0 -18.0 -14.0

In [0]:
dbutils.data.summarize(spark.sql("select * from main.sgfs.auto_judgements_peft_vw"))

<!DOCTYPE html>

In [0]:
%sql
with comparison_data as 
(
select response as peft_response, a.answer as canon_answer, b.answer AS ft_answer from main.sgfs.eval_response_peft_model a
inner join main.sgfs.forum_eval_canonical_data_llama_ft b on a.row_id = b.row_id)
SELECT 
  *,
  ai_query(
    'sg-external', -- this time around we use the CLAUDE 3.7 SONNET
    CONCAT(
      'The following is a comparison of the generated responses from the peft model and the fine-tuned model.',
      'peft model answer:', peft_response, -- peft model
      'fine-tuned answer:', ft_answer, -- fine tuning
      'canonical answer:', canon_answer, -- know it all
      'Your job is to compare the peft model answer with the canonical answer first and produce a score called ''peft_score'' based on how similar they are. Then compare the fine-tuned model answer with the canonical answer and produce a score called ''ft_score''. ',
      'The score should be a number between 0 and 100. The higher the score, the more similar they are. Similarity is based on the coverage of facts in the canonical answer. Similar facts produces a higher score.'
      'Finally produce the following JSON output: {"peft_score": <peft_score> , "ft_score": <ft_score>, "peft_score_reasoning": <peft_score_reasoning>, "ft_score_reasoning": <ft_score_reasoning>}. These are the only keys you need to produce in the JSON. Do not pack the JSON response inside a ```json``` tag. Only produce the JSON and nothing else.'
    )
  ) AS ai_result
FROM comparison_data

peft_response canon_answer ft_answer ai_result To tackle the issue with the rear door locks and gas door not operating, and the central locking system not communicating with the Assenmacher retriever, we'll need to dive into the electrical system of your 1997 BMW 740iL. Given that all fuses are good, our focus will shift towards the central locking module, which is likely the brain behind the locking system's operation.

First, it's essential to consult the wiring diagram specific to your vehicle's make, model, and year. This will provide a clear map of how the central locking module communicates with other components, including the rear door locks and the gas door. The VIN you provided, WBAGJ8325VDL40880, can help ensure you're looking at the correct diagram, as wiring can vary slightly even within the same model year based on production date and optional equipment.

The central locking module, often located in the dashboard or under the steering column, is usually connected to the car's computer system and receives input from various sensors and switches (like the door switches and the central locking button). It then sends output signals to actuators (like the door lock motors and the gas door release).

For pin testing the central locking module, you'll need a multimeter and possibly a wiring diagram that highlights the module's connector pins. Here's a general strategy:

1. **Identify the Module and Its Connector**: Locate the central locking module and its electrical connector. This might require removing trim pieces or the glove box to access.

2. **Consult the Wiring Diagram**: Use the wiring diagram to identify which pins on the connector are associated with the rear door locks and the gas door. Typically, these diagrams are color-coded and can tell you which wire (and thus which pin) is responsible for which function.

3. **Power On and Testing**:
 - With the ignition in the "on" position (but the car not started), use your multimeter to check for voltage at the appropriate pins for the rear door locks and gas door. If you're testing for a signal from the module to the actuators, you might be looking for a pulse or a specific voltage level when the central locking button is pressed.
 - If you find voltage where it should be, the issue might be with the actuators themselves or the wiring between the module and the actuators.
 - If there's no voltage, the problem could be within the central locking module, the wiring, or the control circuit (including switches and sensors).

4. **Ground Testing**: Ensure that the ground circuit for the central locking module and its associated components is good. A faulty ground can prevent the system from working properly.

5. **Signal Testing**: If possible, use an oscilloscope to look at the signal quality coming from the central locking module to the actuators. This can help identify if there's noise on the line or if the signal is not reaching its destination.

6. **Consult a Professional**: If you're not comfortable with this level of electrical diagnosis, or if after testing you're still unsure of the cause, it may be best to consult a professional mechanic or an auto electrician who specializes in BMWs. They will have the necessary experience and possibly specific tools to diagnose and repair the issue efficiently.

Remember, safety first: Ensure you're working in a well-ventilated area, away from any flammable materials, and consider having a fire extinguisher nearby. Also, be cautious not to short circuit any components, as this can cause damage to the vehicle's electrical system. Based on your symptoms with the rear door locks and gas door not operating, here are some troubleshooting steps to follow:

1. First, check the fuses in the trunk near the battery. The fuel door actuator often blows a fuse when it fails, which can disable multiple central locking functions. When checking fuses, be careful as these blade-type fuses can sometimes crack rather than completely blow, giv

In [0]:
_sqldf.createOrReplaceTempView("claude37_results")

In [0]:
_sqldf.write.mode("overwrite").saveAsTable("main.sgfs.auto_judgements_peft_claude37")

In [0]:
%sql
create or replace view main.sgfs.auto_judgements_peft_claude_vw as
select 
get_json_object(ai_result,'$.peft_score') as peft_score,
get_json_object(ai_result,'$.ft_score') as ft_score,
get_json_object(ai_result,'$.peft_score_reasoning') as peft_score_reasoning,
get_json_object(ai_result,'$.ft_score_reasoning') as ft_score_reasoning
from main.sgfs.auto_judgements_peft_claude37;

In [0]:
%sql
select 
avg(peft_score) as avg_peft_score,
avg(ft_score) as avg_ft_score,
median(peft_score) as median_peft_score,
median(ft_score) as median_ft_score,
round((avg(ft_score) - avg(peft_score))/avg(peft_score) * 100) as avg_improvement_percent,
round((median(ft_score) - median(peft_score))/median(peft_score) * 100) as median_improvement_percent
from main.sgfs.auto_judgements_peft_claude_vw;

avg_peft_score avg_ft_score median_peft_score median_ft_score avg_improvement_percent median_improvement_percent 48.5 57.1 42.5 65.0 18.0 53.0

In [0]:
%sql
select avg(avg_peft_score) as jury_avg_peft_score,
avg(avg_ft_score) as jury_avg_fft_score,
avg(median_peft_score) as jury_avg_median_peft_score,
avg(median_ft_score) as jury_avg_median_fft_score
from
(
select 
avg(peft_score) as avg_peft_score,
avg(ft_score) as avg_ft_score,
median(peft_score) as median_peft_score,
median(ft_score) as median_ft_score,
round((avg(ft_score) - avg(peft_score))/avg(peft_score) * 100) as avg_improvement_percent,
round((median(ft_score) - median(peft_score))/median(peft_score) * 100) as median_improvement_percent
from main.sgfs.auto_judgements_peft_claude_vw
union
select 
avg(peft_score) as avg_peft_score,
avg(ft_score) as avg_ft_score,
median(peft_score) as median_peft_score,
median(ft_score) as median_ft_score,
round((avg(ft_score) - avg(peft_score))/avg(peft_score) * 100) as avg_improvement_percent,
round((median(ft_score) - median(peft_score))/median(peft_score) * 100) as median_improvement_percent
from main.sgfs.auto_judgements_peft_vw)
;

jury_avg_peft_score jury_avg_fft_score jury_avg_median_peft_score jury_avg_median_fft_score 57.65 56.05 56.25 62.5